# DSCI 510 Project

Angie Tang

In [472]:
import requests
import pprint
import json
import pandas as pd
from bs4 import BeautifulSoup
import csv
import datetime
from requests.structures import CaseInsensitiveDict

# Define api/Web crawling functions

Data source #1

Rapid api zillow listing data

Includes two steps

Using endpoint/search and endpoint/property

In [993]:
def get_rapid_zillow_api(city, minYear, maxYear):	
    endpoint = "https://zillow69.p.rapidapi.com/search"
    querystring = {"location": f"{city}, CA", "status_type": "RecentlySold",
    "home_type": "Houses, Condos, Townhomes",
    "minPrice": "600000",
    "maxPrice": "5000000",
    "bathsMin": "1",
    "bedsMin": "1",
    "buildYearMin": minYear,
    "buildYearMax": maxYear}
    headers = {
        "X-RapidAPI-Key": "eb078392c0mshb582f825887b6c0p1037d9jsn9dab1abef7e1",
        "X-RapidAPI-Host": "zillow69.p.rapidapi.com",   
    }
    print(f"minYear{minYear}, maxyear{maxYear}")
    response = requests.get(endpoint, headers=headers, params=querystring)
    if response.status_code == 200:
        response_data = response.json()
        pprint.pprint(response_data)
        return response_data
    else:
        print("Error fetching data")
        return[]


In [995]:
def save_search_result():
    data = []
    cities = pd.read_csv("OC_city_names.csv")
    cities = cities['city']
   
    for city in cities:
        minYear = 1970
        maxYear = 1979
        for i in range(1,5):
            source = get_rapid_zillow_api(city, minYear, maxYear)
            if source is not None:
                data.append({'source': source, 'built_year': f"{minYear}s"})
            minYear += 10
            maxYear += 10
            if minYear == 2000:
                maxYear = 2019
    filename = 'zillowapi.json'
    with open(filename, 'w') as f:
        json.dump(data, f)

Data source #2

Geoapify places api

Get places (Park, Grocery Store, School) around a house address

In [1139]:
def get_places_geoapify_api(longitude, latitude):

    # at
    # api_key = '22ef190cdf034a98b197ceeded0e1db9'
    # rb
    # api_key = 'f27b1f01a2c349469713c8d87ba4cc85'
    # g
    api_key = '86e6167d33c343ff9b225be3c9585c16'
    url = f"https://api.geoapify.com/v2/places?categories=leisure.park,commercial.supermarket,education.school&filter=circle:{longitude},{latitude},1400&limit=20&apiKey={api_key}"

    headers = CaseInsensitiveDict()
    headers["Accept"] = "application/json"

    response = requests.get(url, headers=headers)
    if response.status_code == 200:
        response_data = response.json()
        return response_data
    return[]

In [1146]:
def save_places_geoapify():
    coordinates = pd.read_csv('houseSold.csv')
    all_data = []
    features_data = []
    for index, row in coordinates.iterrows():
        longitude = row['longitude']
        latitude = row['latitude']
        zpid = row['zpid']
        address = row['address']
        response_data = get_places_geoapify_api(longitude, latitude)
        features_data = []
        features_data.append({'places around' : address})
        features_data.append({'zpid' : zpid})
        if 'features' in response_data and isinstance(response_data['features'], list):
            for feature in response_data['features']:
                if isinstance(feature, dict): 
                    features_data.append(feature)

        all_data.append(features_data)
    with open('places_around.json', 'w') as json_file:
        json.dump(all_data, json_file, indent=4)

Data source #3

Household income by zip web crawling from

https://localistica.com/usa/ca/county/orange/zipcodes/highest-household-income-zipcodes/#google_vignette

In [883]:
def craw_income_by_zip():
    # headers = {'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/58.0.3029.110 Safari/537.3'}
    base_url = 'https://localistica.com/usa/ca/county/orange/zipcodes/highest-household-income-zipcodes/#google_vignette'
    response = requests.get(base_url)
    response.text
    soup = BeautifulSoup(response.text, 'html')
    print(soup)
    return(soup)

def download_income_by_zip():
    income_by_zip = []
    data = craw_income_by_zip()

    rows = data.find_all('tr')
    for row in rows:
        cells = row.find_all('td')
        if len(cells) >= 6:
            zip_code = cells[0].text.strip()
            income = cells[5].text.strip()
            income_by_zip.append((zip_code, income))
    return income_by_zip


Not a dataset. City names of Orange County

In [711]:
def craw_OC_city_names():
    # headers = {'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/58.0.3029.110 Safari/537.3'}
    base_url = 'https://www.ocgov.com/about-county/info-oc/oc-links/orange-county-links/orange-county-cities'
    response = requests.get(base_url)
    response.text
    soup = BeautifulSoup(response.text, 'html')
    return(soup)

def download_OC_city_names():
    OC_city_names = []
    data = craw_OC_city_names()
    OC_city_names = data.find_all('a',text=lambda text: text and "City of" in text)
    OC_city_names = [(a.text).replace("City of ", "") for a in OC_city_names]
    return OC_city_names

# Store the data

Store data from rapid zillow api

In [1348]:
def csv_results():
    with open('zillowapi.json', 'r') as f:
        data = json.load(f)   
        for item in data:
            built_year = item['built_year']
            for prop in item['source']['props']:
                prop['built_year'] = built_year

        # Normalize the list of properties
        props_data = [prop for item in data for prop in item['source']['props']]
        df = pd.json_normalize(props_data)
        df.to_csv('zillowData_whole.csv', index=False)

def csv_optimal_house_sold_data():
    house_sold = pd.read_csv('zillowData_whole.csv')
    # Days on zillow limit to 180 days since house sold within 180 considered has reasonable price and conditions
    house_sold = house_sold[house_sold['daysOnZillow'] <= 180]
    house_sold = house_sold.drop_duplicates(subset=['zpid'])
    house_sold['zip'] = house_sold['address'].apply(extract_zip)
    house_sold['city'] = house_sold['address'].apply(extract_city)
    house_sold = house_sold[house_sold['zip'].str.contains("CA", na=False)] 
    house_sold['zip'] = house_sold['zip'].str.replace('CA ', '')
    house_sold['year'] = house_sold['variableData.text'].apply(extract_or_assign_year)
    house_sold.head()
    house_sold.to_csv('houseSold.csv', index=False)

def extract_or_assign_year(text):
    if pd.isna(text):
        return datetime.datetime.now().year 
    if isinstance(text, str) and 'Sold' in text:
        return text[-4:] 
    else:
        return datetime.datetime.now().year 

def extract_city(address):
    parts = address.split(',')
    if len(parts) > 1:
        return parts[1].strip()
    else:
        return "City not found"

def extract_zip(address):
    parts = address.split(',')
    if len(parts) > 2:
        return parts[2].strip()
    else:
        return "Zip not found"

Store data from Geoapify places api

In [1316]:
def csv_places():
    with open('places_around.json', 'r') as f:
        data = json.load(f) 

    places_around = {
        'zpid_of_the_house': [],
        'place name': [],
        'category': []
    }
    for ad in data:
        zpid_of_the_house = []
        place_names = []
        category = []

        for item in ad:
            current_zpid = ad[1]['zpid']
            if 'properties' in item:
                name = item['properties'].get('name', None)
                if 'categories' in item['properties']:
                    for c in item['properties']['categories']:
                        if 'supermarket' in c:
                            zpid_of_the_house.append(current_zpid)
                            category.append('grocery store')
                            place_names.append(name)             
                        elif 'park' in c:     
                            zpid_of_the_house.append(current_zpid)
                            category.append('park')
                            place_names.append(name)
                        elif 'school' in c:
                            zpid_of_the_house.append(current_zpid)
                            category.append('school')
                            place_names.append(name)
    
        places_around['zpid_of_the_house'].extend(zpid_of_the_house)
        places_around['place name'].extend(place_names)
        places_around['category'].extend(category)

        
    df = pd.DataFrame(places_around)
    df = df.drop_duplicates(subset=['zpid_of_the_house', 'place name'])  
    df.to_csv('places_around.csv')


Store data from 

https://localistica.com/usa/ca/county/orange/zipcodes/highest-household-income-zipcodes/#google_vignette

In [1369]:
def csv_income_by_zip():
    data = download_income_by_zip()
    df = pd.DataFrame(data, columns=['zip', 'income'])
    df = df.drop(df.index[0])
    df.to_csv('income_by_zip_OC.csv', index = False)

In [982]:
def csv_OC_city_names():
    data = download_OC_city_names()
    df = pd.DataFrame(data, columns=['city'])
    # Due to api limitation, I will drop some small cities 
    # cities_to_remove = ['Seal Beach', 'Stanton', 'Villa Park', 'La Palma', 'Los Alamitos', 'Brea',
    # 'San Juan Capistrano', 'Dana Point', 'Laguna Hills', 'Laguna Woods', 'Cypress', 'Placentia', 'Rancho Santa Margarita']
    # df = df[~df['city'].isin(cities_to_remove)]
    df.to_csv('OC_city_names.csv', index = False)



# Logistic


In [996]:
# Get city names 
csv_OC_city_names()

# Obtain search results from data source #1 Rapid API - search
save_search_result()


/var/folders/tf/n5jbsgms38s6j4s_3kjqk1q40000gn/T/ipykernel_63479/4177595561.py:12: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  OC_city_names = data.find_all('a',text=lambda text: text and "City of" in text)


minYear1970, maxyear1979
{'currentPage': 1,
 'props': [{'address': '24792 Via San Rafael, Aliso Viejo, CA 92656',
            'bathrooms': 2,
            'bedrooms': 3,
            'contingentListingType': None,
            'country': 'USA',
            'currency': 'USD',
            'dateSold': 1711609200000,
            'daysOnZillow': 17,
            'detailUrl': '/homedetails/24792-Via-San-Rafael-Aliso-Viejo-CA-92656/25542243_zpid/',
            'hasImage': True,
            'imgSrc': 'https://photos.zillowstatic.com/fp/d85b279b65f8d8134a515637837fb782-p_e.jpg',
            'latitude': 33.602184,
            'listingStatus': 'RECENTLY_SOLD',
            'listingSubType': {},
            'livingArea': 1240,
            'longitude': -117.722595,
            'lotAreaUnit': 'sqft',
            'lotAreaValue': 2447,
            'price': 670000,
            'propertyType': 'SINGLE_FAMILY',
            'rentZestimate': 3814,
            'variableData': {'text': 'Sold 03/28/2024',
        

In [1349]:
csv_results()
csv_optimal_house_sold_data()

In [1147]:
save_places_geoapify()
# 34 mins
# place_around.csv

In [1377]:
csv_places()

In [1378]:
csv_income_by_zip()

<!DOCTYPE HTML PUBLIC "-//W3C//DTD HTML 4.0 Transitional//EN">
<html>
<head>
<title>
        Highest Income Zip Codes in Orange County of California State (CA) | Localistica.com</title>
<meta content="highest income zip codes in orange county,orange, ca, california ,population, esitmated population, census, growth, all zip codes, area codes, time zones, counties, metro areas, male ratio, female ratio, income by state, households, localistica.com" name="keywords"/>
<meta content="Information for Orange California state - population, growth, income, time zone, area codes on localistica.com" name="description"/>
<link href="http://localistica.com/favicon.ico" rel="shotrcut icon" type="image/ico"/>
<meta charset="utf-8"/>
<meta content="IE=edge" http-equiv="X-UA-Compatible"/>
<meta content="width=device-width, initial-scale=1, shrink-to-fit=no" name="viewport"/>
<!--    <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/bootstrap/3.3.7/css/bootstrap.min.css" integrity="sha384-BVY

In [763]:
# search_result = pd.read_csv('zillowData.csv')
# len(search_result)
# search_result['zpid'].duplicated().sum()

4305

# Data Model

In [1327]:
import sqlite3
import datetime
import pandas as pd

In [1382]:
def house_sold_table():
    conn = sqlite3.connect('510project.db', detect_types=sqlite3.PARSE_DECLTYPES|sqlite3.PARSE_COLNAMES)
    cur = conn.cursor()
    df = pd.read_csv("houseSold.csv")
    
    cur.execute('DROP TABLE IF EXISTS HOUSES')
    cur.execute(
        '''
        CREATE TABLE IF NOT EXISTS HOUSES (
            zpid TEXT PRIMARY KEY,
            city TEXT,
            zipcode TEXT,
            yearSold INTEGER,
            propertyType TEXT,
            price REAL,
            bedrooms INTEGER,
            bathrooms INTEGER,
            livingArea REAL,
            builtYear TEXT,
            longitude TEXT,
            latitude TEXT,
            FOREIGN KEY (zipcode) REFERENCES OCINCOMEBYZIP(zipcode)

        )''')
    
    for index, row in df.iterrows():
        zpid = row['zpid']
        city = row['city']
        zipcode = row['zip']
        yearSold = row['year']
        propertyType = row['propertyType']
        price = row['price'] 
        bedrooms = row['bedrooms']
        bathrooms = row['bathrooms']
        livingArea = row['livingArea']  
        builtYear = row['built_year']
        longitude = row['longitude']
        latitude = row['latitude']

        cur.execute(
            'INSERT INTO HOUSES (zpid, city, zipcode, yearSold, propertyType, price, bedrooms, bathrooms, livingArea, builtYear, longitude, latitude) VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)', 
        (zpid, city, zipcode, yearSold, propertyType, price, bedrooms, bathrooms, livingArea, builtYear,longitude, latitude))
    
    table = pd.read_sql_query('SELECT * FROM HOUSES LIMIT 5', conn)
    print(table)
    

    conn.commit()
    conn.close()

In [1380]:
def places_table():
    conn = sqlite3.connect('510project.db', detect_types=sqlite3.PARSE_DECLTYPES|sqlite3.PARSE_COLNAMES)
    cur = conn.cursor()
    df = pd.read_csv("places_around.csv")
    
    cur.execute('DROP TABLE IF EXISTS PLACESAROUND')
    cur.execute(
        '''
        CREATE TABLE IF NOT EXISTS PLACESAROUND (
            id INTEGER PRIMARY KEY AUTOINCREMENT,
            zpid TEXT,
            name TEXT,
            category TEXT,
            FOREIGN KEY (zpid) REFERENCES HOUSES(zpid)
        )''')
    
    for index, row in df.iterrows():
        zpid = row['zpid_of_the_house']
        name = row['place name']
        category = row['category']

        cur.execute(
            'INSERT INTO PLACESAROUND (zpid, name, category) VALUES (?, ?, ?)', 
        (zpid, name, category))
    
    table = pd.read_sql_query('SELECT * FROM PLACESAROUND LIMIT 5', conn)
    print(table)
    
    conn.commit()
    conn.close()

In [1383]:
def OC_income_zip_table():
    conn = sqlite3.connect('510project.db', detect_types=sqlite3.PARSE_DECLTYPES|sqlite3.PARSE_COLNAMES)
    cur = conn.cursor()
    df = pd.read_csv("income_by_zip_OC.csv")
    
    cur.execute('DROP TABLE IF EXISTS OCINCOMEBYZIP')
    cur.execute(
        '''
        CREATE TABLE IF NOT EXISTS OCINCOMEBYZIP (
            zipcode TEXT PRIMARY KEY,
            income TEXT
        )''')
    
    for index, row in df.iterrows():
        zipcode = row['zip']
        income = row['income']

        cur.execute(
            'INSERT INTO OCINCOMEBYZIP (zipcode, income) VALUES (?, ?)', 
        (zipcode, income))
    
    table = pd.read_sql_query('SELECT * FROM OCINCOMEBYZIP LIMIT 5', conn)
    print(table)
    
    conn.commit()
    conn.close()

In [1384]:
house_sold_table()

       zpid         city zipcode  yearSold   propertyType     price  bedrooms  \
0  25542243  Aliso Viejo   92656      2024  SINGLE_FAMILY 670000.00         3   
1  25542306  Aliso Viejo   92656      2024  SINGLE_FAMILY 632000.00         3   
2  25542498  Aliso Viejo   92656      2024  SINGLE_FAMILY 720000.00         3   
3  25542327  Aliso Viejo   92656      2024      TOWNHOUSE 675000.00         3   
4  25542140  Aliso Viejo   92656      2024  SINGLE_FAMILY 715000.00         3   

   bathrooms  livingArea builtYear    longitude   latitude  
0          2     1240.00     1970s  -117.722595  33.602184  
1          2     1240.00     1970s   -117.72207  33.601254  
2          2     1240.00     1970s    -117.7205   33.60195  
3          2     1240.00     1970s   -117.72102   33.60096  
4          2     1240.00     1970s   -117.72023   33.60348  


In [1385]:
places_table()

   id      zpid                                    name       category
0   1  25542243                                    ALDI  grocery store
1   2  25542243  Aliso and Wood Canyons Wilderness Park           park
2   3  25542243                         Mother's Market  grocery store
3   4  25542243                          Brookline Park           park
4   5  25542243                          Creekside Park           park


In [1386]:
OC_income_zip_table()

  zipcode       income
0   92861  $116,658.00
1   92657  $114,004.00
2   92679  $112,998.00
3   92602  $112,399.00
4   92694  $104,306.00


# EDA

In [ ]:
# import numpy as np
# from sklearn.linear_model import LinearRegression

In [1249]:
# house_simple_data = pd.read_csv('zillowData.csv')
# house_simple_data = house_simple_data[house_simple_data['daysOnZillow'] <= 180 ]
# house_simple_data = house_simple_data[['address', 'propertyType', 'built_year', 'price', 'bedrooms', 'bathrooms', 'livingArea', 'variableData.text']]
# income_oc = pd.read_csv('income_by_zip_OC.csv')
# len(house_simple_data)

2885

In [ ]:
# pivot_df = places.pivot_table(index='zpid_of_the_house', 
#                           columns='category', 
#                           values='place name', 
#                           aggfunc=lambda x: ', '.join(map(str, x.dropna().unique())))
# pivot_df.fillna('NA', inplace=True)
# pivot_df.reset_index(inplace=True)
# pivot_df.rename_axis(None, axis=1, inplace=True)



In [1237]:
# house_simple_data = pd.read_csv('houseSold.csv')
# # house_simple_data = house_simple_data[house_simple_data['daysOnZillow'] <= 180 ]
# house_simple_data = house_simple_data[['address', 'zpid', 'propertyType', 'built_year', 'price', 'bedrooms', 'bathrooms', 'livingArea', 'variableData.text']]
# income_oc = pd.read_csv('income_by_zip_OC.csv')
# places_around = pd.read_csv('places_around.csv')
# len(house_simple_data)

2885

In [1252]:
# house_simple_data['built_year'] = house_simple_data['built_year'].str[:-1].astype(int)

In [1253]:
# house_simple_data = house_simple_data.drop('address', axis = 1)
# house_simple_data = house_simple_data.drop('variableData.text', axis = 1)
# house_simple_data.head()

propertyType  built_year   price  bedrooms  bathrooms  livingArea    zip  \
0  SINGLE_FAMILY        1970  670000         3       2.00        1240  92656   
1  SINGLE_FAMILY        1970  632000         3       2.00        1240  92656   
2  SINGLE_FAMILY        1970  720000         3       2.00        1240  92656   
3      TOWNHOUSE        1970  675000         3       2.00        1240  92656   
4  SINGLE_FAMILY        1970  715000         3       2.00        1240  92656   

          city  year  
0  Aliso Viejo  2024  
1  Aliso Viejo  2024  
2  Aliso Viejo  2024  
3  Aliso Viejo  2024  
4  Aliso Viejo  2024

In [1254]:
# house_simple_data = pd.merge(house_simple_data, income_oc, on='zip', how='left')
# # house_simple_data = pd.merge(house_simple_data, places_around, on='zpid', how='left')
# house_simple_data.tail()

propertyType  built_year    price  bedrooms  bathrooms  livingArea  \
2880  SINGLE_FAMILY        2000  2300000         5       5.00        4823   
2881          CONDO        2000  1080000         3       3.00        1702   
2882  SINGLE_FAMILY        2000  2275000         4       5.00        3600   
2883  SINGLE_FAMILY        2000  3050000         5       5.00        4550   
2884          CONDO        2000  1192000         4       3.00        2449   

        zip         city  year       income  
2880  92887  Yorba Linda  2023  $103,926.00  
2881  92886  Yorba Linda  2023   $82,188.00  
2882  92886  Yorba Linda  2023   $82,188.00  
2883  92886  Yorba Linda  2023   $82,188.00  
2884  92886  Yorba Linda  2023   $82,188.00

In [1255]:
# house_simple_data['income'] = house_simple_data['income'].replace(r'[\$,]', '', regex=True).astype(float)
# house_simple_data.tail()

propertyType  built_year    price  bedrooms  bathrooms  livingArea  \
2880  SINGLE_FAMILY        2000  2300000         5       5.00        4823   
2881          CONDO        2000  1080000         3       3.00        1702   
2882  SINGLE_FAMILY        2000  2275000         4       5.00        3600   
2883  SINGLE_FAMILY        2000  3050000         5       5.00        4550   
2884          CONDO        2000  1192000         4       3.00        2449   

        zip         city  year    income  
2880  92887  Yorba Linda  2023 103926.00  
2881  92886  Yorba Linda  2023  82188.00  
2882  92886  Yorba Linda  2023  82188.00  
2883  92886  Yorba Linda  2023  82188.00  
2884  92886  Yorba Linda  2023  82188.00

In [828]:
# columns_to_check = ['price', 'livingArea', 'bedrooms', 'bathrooms']

# # Applying the IQR method for each column
# for column in columns_to_check:
#     Q1 = house_simple_data[column].quantile(0)
#     Q3 = house_simple_data[column].quantile(0.85)
#     IQR = Q3 - Q1
#     lower_bound = Q1 - 1.5 * IQR
#     upper_bound = Q3 + 1.5 * IQR
    
#     # Update the DataFrame by filtering out outliers in the current column
#     house_simple_data = house_simple_data[(house_simple_data[column] >= lower_bound) & (house_simple_data[column] <= upper_bound)]

In [806]:
# Q1 = house_simple_data['price'].quantile(0.15)
# Q3 = house_simple_data['price'].quantile(0.85)
# IQR = Q3 - Q1

# # Define outliers using 1.5*IQR criteria
# lower_bound = Q1 - 1.5 * IQR
# upper_bound = Q3 + 1.5 * IQR

# # Filter out outliers
# house_simple_data = house_simple_data[(house_simple_data['price'] >= lower_bound) & (house_simple_data['price'] <= upper_bound)]
# len(house_simple_data)
# len(house_simple_data)


3834

In [1197]:
# house_simple_data.to_csv('house_simple_data.csv', index=False)

In [905]:
# house_simple_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3964 entries, 0 to 3963
Data columns (total 9 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   propertyType  3964 non-null   object 
 1   price         3964 non-null   int64  
 2   bedrooms      3964 non-null   int64  
 3   bathrooms     3964 non-null   float64
 4   livingArea    3964 non-null   float64
 5   zip           3964 non-null   object 
 6   city          3964 non-null   object 
 7   year          3964 non-null   object 
 8   income        3960 non-null   float64
dtypes: float64(3), int64(2), object(4)
memory usage: 278.8+ KB


In [1200]:
# df.head()

zpid   propertyType  built_year   price  bedrooms  bathrooms  \
0  25542243  SINGLE_FAMILY        1970  670000         3       2.00   
1  25542306  SINGLE_FAMILY        1970  632000         3       2.00   
2  25542498  SINGLE_FAMILY        1970  720000         3       2.00   
3  25542327      TOWNHOUSE        1970  675000         3       2.00   
4  25542140  SINGLE_FAMILY        1970  715000         3       2.00   

   livingArea    zip         city  year   income  \
0        1240  92656  Aliso Viejo  2024 74688.00   
1        1240  92656  Aliso Viejo  2024 74688.00   
2        1240  92656  Aliso Viejo  2024 74688.00   
3        1240  92656  Aliso Viejo  2024 74688.00   
4        1240  92656  Aliso Viejo  2024 74688.00   

                                       address  places around  
0  24792 Via San Rafael, Aliso Viejo, CA 92656  grocery store  
1       23375 El Reposa, Aliso Viejo, CA 92656  grocery store  
2     23466 Los Adornos, Aliso Viejo, CA 92656  grocery store  
3       23431 El Reposa, Aliso Viejo, CA 92656  grocery store  
4     23495 Via Jacinto, Aliso Viejo, CA 92656  grocery store

In [1258]:
# df = house_simple_data.drop('zip', axis=1)
# df = df.drop('income', axis=1)
# # df = df.drop('zpid', axis=1)
# # df = df.drop('address', axis=1)
# # df = df.drop('Unnamed: 0', axis=1)
# # df = df.drop('places around', axis=1)
# df.dropna(inplace=True)
# df_encoded = pd.get_dummies(df, columns=['propertyType', 'city'])

# # Separate features and target
# X = df_encoded.drop('price', axis=1)
# y = df_encoded['price']
# model = LinearRegression()

In [1259]:
# df.head()

propertyType  built_year   price  bedrooms  bathrooms  livingArea  \
0  SINGLE_FAMILY        1970  670000         3       2.00        1240   
1  SINGLE_FAMILY        1970  632000         3       2.00        1240   
2  SINGLE_FAMILY        1970  720000         3       2.00        1240   
3      TOWNHOUSE        1970  675000         3       2.00        1240   
4  SINGLE_FAMILY        1970  715000         3       2.00        1240   

          city  year  
0  Aliso Viejo  2024  
1  Aliso Viejo  2024  
2  Aliso Viejo  2024  
3  Aliso Viejo  2024  
4  Aliso Viejo  2024

In [1260]:
# from sklearn.model_selection import train_test_split

# # Split the data into training and testing sets
# X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)


In [1261]:
# model.fit(X_train, y_train)
# from sklearn.metrics import mean_squared_error, r2_score
# y_pred = model.predict(X_test)

# # Evaluate the model
# mse = mean_squared_error(y_test, y_pred)
# r2 = r2_score(y_test, y_pred)

# print(f"Mean Squared Error: {mse}")
# print(f"R^2 Score: {r2}")

Mean Squared Error: 126387360974.43658
R^2 Score: 0.8083173794799726


In [1235]:
# from sklearn.linear_model import Ridge

# # Example usage:
# # alpha is the regularization strength
# ridge_model = Ridge(alpha=1.0)
# ridge_model.fit(X_train, y_train)

# y_pred = ridge_model.predict(X_test)

# # Evaluate the model
# mse = mean_squared_error(y_test, y_pred)
# r2 = r2_score(y_test, y_pred)

# print(f"Mean Squared Error: {mse}")
# print(f"R^2 Score: {r2}")


Mean Squared Error: 125450779730.24933
R^2 Score: 0.8097378248934348


In [1055]:
# from sklearn.linear_model import Lasso

# # Example usage:
# lasso_model = Lasso(alpha=0.1)
# lasso_model.fit(X_train, y_train)

# y_pred =lasso_model.predict(X_test)

# # Evaluate the model
# mse = mean_squared_error(y_test, y_pred)
# r2 = r2_score(y_test, y_pred)

# print(f"Mean Squared Error: {mse}")
# print(f"R^2 Score: {r2}")


Mean Squared Error: 126371487617.45082
R^2 Score: 0.8083414534588897


/Users/guotang/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/linear_model/_coordinate_descent.py:678: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.708e+14, tolerance: 1.553e+11
  model = cd_fast.enet_coordinate_descent(


In [821]:
# df_encoded.head()

price  bedrooms  bathrooms  livingArea  year  propertyType_CONDO  \
0  1755000         4       3.00     2100.00  2024               False   
1  1429500         4       3.00     1933.00  2024               False   
2   962000         3       3.00     1499.00  2024                True   
3  1225000         3       3.00     1984.00  2024                True   
4   855000         2       3.00     1291.00  2024                True   

   propertyType_SINGLE_FAMILY  propertyType_TOWNHOUSE  city_Aliso Viejo  \
0                        True                   False              True   
1                        True                   False              True   
2                       False                   False              True   
3                       False                   False              True   
4                       False                   False              True   

   city_Anaheim  city_Buena Park  city_Costa Mesa  city_Fountain Valley  \
0         False            False            False                 False   
1         False            False            False                 False   
2         False            False            False                 False   
3         False            False            False                 False   
4         False            False            False                 False   

   city_Fullerton  city_Garden Grove  city_Huntington Beach  city_Irvine  \
0           False              False                  False        False   
1           False              False                  False        False   
2           False              False                  False        False   
3           False              False                  False        False   
4           False              False                  False        False   

   city_La Habra  city_Laguna Beach  city_Laguna Niguel  city_Lake Forest  \
0          False              False               False             False   
1          False              False               False             False   
2          False              False               False             False   
3          False              False               False             False   
4          False              False               False             False   

   city_Mission Viejo  city_Newport Beach  city_Orange  city_San Clemente  \
0               False               False        False              False   
1               False               False        False              False   
2               False               False        False              False   
3               False               False        False              False   
4               False               False        False              False   

   city_Santa Ana  city_Tustin  city_Westminster  city_Yorba Linda  
0           False        False             False             False  
1           False        False             False             False  
2           False        False             False             False  
3           False        False             False             False  
4           False        False             False             False

In [1264]:
# columns = df_encoded.drop('price', axis=1).columns
# new_data = pd.DataFrame({
#     'year': [2023],
#     'bedrooms': [3],
#     'city_Irvine': [1],
#     'bathrooms': [2],
#     'built_year': [1980],
#     'livingArea': [1400],
#     'propertyType_CONDO': [1],   # Since it's a condo
#     'propertyType_SINGLE_FAMILY': [0]  # Not a single family home
# }, columns=columns) 
# new_data.fillna(False, inplace=True)
# predicted_price = model.predict(new_data)
# print(f"Predicted Price: ${predicted_price[0]:,.2f}")

Predicted Price: $1,196,725.33


/var/folders/tf/n5jbsgms38s6j4s_3kjqk1q40000gn/T/ipykernel_63479/2903819538.py:12: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  new_data.fillna(False, inplace=True)
